In [1]:
import cv2
import argparse
import imutils
import time
import scipy.io
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import accuracy_score
from sklearn.model_selection import GridSearchCV
from random import shuffle
import numpy as np
import mahotas
import os

In [2]:
im = cv2.imread('../Youtube-Objects/bird/00004183.jpg',cv2.IMREAD_COLOR)
bird_ranges = scipy.io.loadmat('../Youtube-Objects/Ranges/ranges_bird.mat')
bb_gt = scipy.io.loadmat('../Youtube-Objects/GroundTruth/bird/bb_gtTraining_bird.mat')
bb_test_gt = scipy.io.loadmat('../Youtube-Objects/GroundTruth/bird/bb_gtTest_bird.mat')

In [3]:
bird_ranges['ranges']

array([[    1,   410,  3282,  3282,  5472,  5585,  5607,  5698,  5761,
         5986,  6118,  6206,  6231,  6386,  6407,  6477,  6500,  6546,
         6567,  6588,  6643,  6651,  6655,  6658,  6662,  6666,  6669,
         6671,  6673,  6675,  6678,  6681,  6683,  6686,  6688,  6691,
         6693,  6696,  6698,  6700,  6704,  6707,  6709,  6711,  6713,
         6717,  6720,  6722,  6725,  6729,  7024,  7027,  7031,  7036,
         7043,  7047,  7053,  7058,  7063,  7066,  7069,  7071,  7074,
         7083, 10821, 10824, 10826, 10828, 10832, 10835, 10838, 10842,
        10848, 10853, 10856, 10858, 10862, 10865, 10868, 10871, 10873,
        10877, 10880, 11301, 11305, 11309, 11311, 11313, 11317, 11319,
        11321, 11324, 11326, 11329, 11332, 11335, 11337, 11341, 11344,
        11346, 11349, 11351, 11353, 11355, 11358, 11362, 11365, 11368,
        11371, 11375, 11399, 11491, 11494, 13878, 13880, 13883, 13893,
        13897, 13900, 14057, 14127, 14710, 14715, 14717, 15795, 15904,
      

In [4]:
# cv2.imshow('img',cv2.resize(im,(256, 256), interpolation = cv2.INTER_CUBIC))
# cv2.waitKey(0)
# cv2.destroyAllWindows()

In [5]:
bb_gt['bb_gtTraining']

# for i in range(len(bb_gt['bb_gtTraining'][0])):
#     if(bb_gt['bb_gtTraining'][0][i][0]=='bird00004371'):
#         print(bb_gt['bb_gtTraining'][0][i][0])
#         print(bb_gt['bb_gtTraining'][0][i][1][0])
#     print(i)

array([[(array(['bird00004183'], dtype='<U12'), array([[ 727,  110, 1120,  418]], dtype=uint16)),
        (array(['bird00004188'], dtype='<U12'), array([[ 737,  107, 1119,  418]], dtype=uint16)),
        (array(['bird00004189'], dtype='<U12'), array([[ 732,  100, 1118,  424]], dtype=uint16)),
        (array(['bird00004192'], dtype='<U12'), array([[ 738,  104, 1088,  427]], dtype=uint16)),
        (array(['bird00004198'], dtype='<U12'), array([[ 738,  102, 1082,  426]], dtype=uint16)),
        (array(['bird00004202'], dtype='<U12'), array([[ 738,   99, 1083,  430]], dtype=uint16)),
        (array(['bird00004204'], dtype='<U12'), array([[ 738,  102, 1081,  431]], dtype=uint16)),
        (array(['bird00004212'], dtype='<U12'), array([[ 753,   54, 1010,  434]], dtype=uint16)),
        (array(['bird00004213'], dtype='<U12'), array([[ 754,   55, 1006,  433]], dtype=uint16)),
        (array(['bird00004216'], dtype='<U12'), array([[ 769,  126, 1014,  434]], dtype=uint16)),
        (array(['bir

In [6]:
bb_test_gt
# bb_test_gt['bb_gtTest'][0][0][1][0]

{'__globals__': [],
 '__header__': b'MATLAB 5.0 MAT-file, Platform: GLNXA64, Created on: Wed Feb 25 21:06:56 2015',
 '__version__': '1.0',
 'bb_gtTest': array([[(array(['bird00000006'], dtype='<U12'), array([[608,  29, 834, 638]], dtype=uint16)),
         (array(['bird00000044'], dtype='<U12'), array([[600,  28, 868, 639]], dtype=uint16)),
         (array(['bird00000089'], dtype='<U12'), array([[511,  80, 901, 658]], dtype=uint16)),
         (array(['bird00000138'], dtype='<U12'), array([[602, 100, 861, 640]], dtype=uint16)),
         (array(['bird00000144'], dtype='<U12'), array([[605,  95, 862, 650]], dtype=uint16)),
         (array(['bird00000171'], dtype='<U12'), array([[602,  96, 862, 645]], dtype=uint16)),
         (array(['bird00000208'], dtype='<U12'), array([[600,  97, 861, 645]], dtype=uint16)),
         (array(['bird00000258'], dtype='<U12'), array([[533, 102, 892, 661]], dtype=uint16)),
         (array(['bird00000282'], dtype='<U12'), array([[549, 118, 894, 656]], dtype=uin

In [7]:
def fd_hu_moments(image):
    image = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    feature = cv2.HuMoments(cv2.moments(image)).flatten()
    return feature

def fd_haralick(image):    # convert the image to grayscale
    gray = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    # compute the haralick texture feature vector
    haralick = mahotas.features.haralick(gray).mean(axis=0)
    return haralick

def fd_histogram(image, mask=None):
    # convert the image to HSV color-space
#     image = cv2.cvtColor(image, cv2.COLOR_BGR2HSV)
#     # compute the color histogram
#     hist  = cv2.calcHist([image], [0, 1, 2], None, [bins, bins, bins], [0, 256, 0, 256, 0, 256])
#     # normalize the histogram
#     cv2.normalize(hist, hist)
#     hist.flatten()
    
    hsv_roi =  cv2.cvtColor(image, cv2.COLOR_BGR2HSV)
    mask = cv2.inRange(hsv_roi, np.array((0., 60.,32.)), np.array((180.,255.,255.)))
    roi_hist = cv2.calcHist([hsv_roi],[0],mask,[180],[0,180])
    cv2.normalize(roi_hist,roi_hist,0,255,cv2.NORM_MINMAX)
    return roi_hist

In [ ]:
fname = ''
i=11494
start = None
end = None
label=None
N=34518
while i<N:
#     j=0
    fname = ''
    for j in range(8-len(str(i))):
        fname=fname+'0'
    fname=fname+str(i)
    im = cv2.imread('../Youtube-Objects/bird/'+fname+'.jpg',cv2.IMREAD_COLOR)
    
    for z in range(len(bird_ranges['ranges'][0])):
        if(i==bird_ranges['ranges'][0][z]):
            start = bird_ranges['ranges'][0][z]
        if(i>=bird_ranges['ranges'][0][z] and i<=bird_ranges['ranges'][1][z]):
            label=bird_ranges['ranges'][2][z]
            end = bird_ranges['ranges'][1][z]
            N=end
        frame = imutils.resize(im, width=500)
        cv2.imshow(str(label)+'img',frame)
        key = cv2.waitKey(1) & 0xFF
    # if the `q` key was pressed, break from the loop
        if key == ord("q"):
            break
    i=i+1
cv2.destroyAllWindows()

In [8]:
fname = ''
i=4183
bbox=None
start = None
end = None
X=None
label=None
TEST=None
test_box=None
GT=None
Y=None
N=34518
while i<N:
#     j=0
    fname = ''
    for j in range(8-len(str(i))):
        fname=fname+'0'
    fname=fname+str(i)
    im = cv2.imread('../Youtube-Objects/bird/'+fname+'.jpg',cv2.IMREAD_COLOR)
    
    for z in range(len(bird_ranges['ranges'][0])):
        if(i==bird_ranges['ranges'][0][z]):
            start = bird_ranges['ranges'][0][z]
        if(i>=bird_ranges['ranges'][0][z] and i<=bird_ranges['ranges'][1][z]):
            label=bird_ranges['ranges'][2][z]
#             end = bird_ranges['ranges'][1][z]
    
    if start is not None:
        if i==start:
            bbox=None
    
    for k in range(len(bb_gt['bb_gtTraining'][0])):
        if(bb_gt['bb_gtTraining'][0][k][0]=='bird'+fname):
            bbox=bb_gt['bb_gtTraining'][0][k][1][0]
    for k in range(len(bb_test_gt['bb_gtTest'][0])):
        if(bb_test_gt['bb_gtTest'][0][k][0]=='bird'+fname):
            test_box=bb_test_gt['bb_gtTest'][0][k][1][0]
    
#         print(bb_gt['bb_gtTraining'][0][k][0])
#         print(bb_gt['bb_gtTraining'][0][k][1][0])
    if test_box is not None:
        (x,y,w,h) = test_box
#         cv2.rectangle(im, (x, y), (w,h),(0, 255, 0), 2)
        cropped_im = im[y:h,x:w]
        f1 = fd_histogram(cropped_im)
        f2 = fd_haralick(cropped_im)
        f3 = fd_hu_moments(cropped_im)
        a=f1.tolist()
        b=np.zeros(len(a))
        for ind in range(len(a)):
            b[ind] = a[ind][0]
        # global_feature = [f1,f2,f3]
        if max(b)!=0:
            b = (b - min(b))/max(b)
        if max(f2)!=0:
            f2 = (f2 - min(f2))/max(f2)
        if max(f3)!=0:
            f3 = (f3 - min(f3))/max(f3)
        global_feature = np.hstack([b,f2,f3])
        if TEST is not None:
            TEST.append(global_feature)
        else:
            TEST=[global_feature]
            
        if GT is not None:
            GT.append(label)
        else:
            GT=[label]
    if bbox is not None:
        (x,y,w,h) = bbox
#         cv2.rectangle(im, (x, y), (w,h),(0, 255, 0), 2)
        cropped_im = im[y:h,x:w]
        f1 = fd_histogram(cropped_im)
        f2 = fd_haralick(cropped_im)
        f3 = fd_hu_moments(cropped_im)
        a=f1.tolist()
        b=np.zeros(len(a))
        for ind in range(len(a)):
            b[ind] = a[ind][0]
        # global_feature = [f1,f2,f3]
        if max(b)!=0:
            b = (b - min(b))/max(b)
        if max(f2)!=0:
            f2 = (f2 - min(f2))/max(f2)
        if max(f3)!=0:
            f3 = (f3 - min(f3))/max(f3)
        global_feature = np.hstack([b,f2,f3])
        if X is not None:
            X.append(global_feature)
        else:
            X=[global_feature]
            
        if Y is not None:
            Y.append(label)
        else:
            Y=[label]
#         gray= cv2.cvtColor(cropped_im,cv2.COLOR_BGR2GRAY)
#         sift = cv2.xfeatures2d.SIFT_create()
#         kp = sift.detect(gray,None) 
#         img=cv2.drawKeypoints(cropped_im,kp)

#         cropped_im=cv2.resize(cropped_im,(256, 256), interpolation = cv2.INTER_CUBIC)

#     cv2.imshow('img',cv2.resize(im,(256, 256), interpolation = cv2.INTER_CUBIC))
#     cv2.imshow('img',im)
        cv2.imshow('img',cropped_im)
        key = cv2.waitKey(1) & 0xFF
    # if the `q` key was pressed, break from the loop
        if key == ord("q"):
            break
    i=i+1
cv2.destroyAllWindows()
#     print(fname)

In [7]:
# cv2.imshow('img',im[y:h,x:w])
# cv2.waitKey(0)
# cv2.destroyAllWindows()

In [9]:
np.unique(Y)

array([ 2,  3,  4,  5,  6,  7,  9, 11, 12, 14], dtype=uint16)

In [10]:
len(X)

16466

In [11]:
len(TEST)

14445

In [10]:
np.unique(GT)

array([ 1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16],
      dtype=uint16)

In [178]:
# f1 = fd_histogram(im[y:h,x:w])
# f2 = fd_haralick(im[y:h,x:w])
# f3 = fd_hu_moments(im[y:h,x:w])
# a=f1.tolist()
# b=np.zeros(len(a))
# for i in range(len(a)):
#     b[i] = a[i][0]
# # global_feature = [f1,f2,f3]
# b = (b - min(b))/max(b)
# f2 = (f2 - min(f2))/max(f2)
# f3 = (f3 - min(f3))/max(f3)
# global_feature = np.hstack([b,f2,f3])
# # resized_im=cv2.resize(im[y:h,x:w],(256, 256), interpolation = cv2.INTER_CUBIC)
# # f1,f2,f3 = fd_histogram(resized_im), fd_haralick(resized_im), fd_hu_moments(resized_im)
# # global_feature = np.hstack([fd_histogram(resized_im), fd_haralick(resized_im), fd_hu_moments(resized_im)])
# # scaler = MinMaxScaler(feature_range=(0, 1))
# #Normalize The feature vectors...
# # rescaled_features = scaler.fit_transform(global_feature)

In [177]:
# a = np.array([global_feature,global_feature])
# for i in range(10):
#     a = a.append(global_feature)
# a.shape

AttributeError: 'numpy.ndarray' object has no attribute 'append'

In [184]:
# a=None
# a=[global_feature]
# a.append(global_feature)
# a

[array([6.46907247e-02, 8.01546407e-02, 1.05927836e-01, 8.37628882e-02,
        9.92268042e-02, 1.63402059e-01, 5.79896924e-02, 3.81443308e-02,
        1.02319589e-01, 1.28350524e-01, 3.96907232e-02, 8.60824711e-02,
        8.78865986e-02, 4.61340203e-02, 3.50515461e-02, 7.29381455e-02,
        5.28350525e-02, 3.29896909e-02, 1.52061855e-02, 3.47938147e-02,
        2.21649482e-02, 2.98969081e-02, 4.04639175e-02, 1.49484540e-02,
        4.07216489e-02, 5.92783515e-03, 3.96907232e-02, 1.41752579e-02,
        9.02061890e-03, 1.54639179e-02, 1.34020617e-02, 7.73195893e-03,
        1.67525769e-02, 1.05670103e-02, 1.13402065e-02, 3.55670090e-02,
        1.57216493e-02, 1.26288665e-02, 2.19072168e-02, 2.91237119e-02,
        2.34536091e-02, 3.60824756e-02, 3.37628852e-02, 1.08247427e-01,
        1.79896915e-01, 2.77319592e-01, 4.79896903e-01, 5.38917544e-01,
        7.01030938e-01, 1.00000000e+00, 8.40721629e-01, 7.72164963e-01,
        6.69845382e-01, 5.55412356e-01, 3.32216500e-01, 3.376288

In [13]:
# svc = SVC(C=9,kernel='poly',probability=True)
# svc.fit(train_X,train_y)
# train_predictions = svc.predict(val_X)

NameError: name 'train_X' is not defined

In [209]:
# scores=[]
# n=5
# for i in range(n):
#     train_X, val_X, train_y, val_y = train_test_split(X, Y)
#     svc = SVC(C=9,kernel='poly',probability=True)
#     svc.fit(train_X,train_y)
#     train_predictions = svc.predict(val_X)
#     s=accuracy_score(val_y, train_predictions)
#     scores.append(s)

# accuracy = np.mean(scores)
# print("Accuracy:"+str(accuracy))

/usr/local/lib/python3.6/dist-packages/sklearn/svm/base.py:196: FutureWarning: The default value of gamma will change from 'auto' to 'scale' in version 0.22 to account better for unscaled features. Set gamma explicitly to 'auto' or 'scale' to avoid this warning.
  "avoid this warning.", FutureWarning)
/usr/local/lib/python3.6/dist-packages/sklearn/svm/base.py:196: FutureWarning: The default value of gamma will change from 'auto' to 'scale' in version 0.22 to account better for unscaled features. Set gamma explicitly to 'auto' or 'scale' to avoid this warning.
  "avoid this warning.", FutureWarning)
/usr/local/lib/python3.6/dist-packages/sklearn/svm/base.py:196: FutureWarning: The default value of gamma will change from 'auto' to 'scale' in version 0.22 to account better for unscaled features. Set gamma explicitly to 'auto' or 'scale' to avoid this warning.
  "avoid this warning.", FutureWarning)
/usr/local/lib/python3.6/dist-packages/sklearn/svm/base.py:196: FutureWarning: The default 

NameError: name 'mean' is not defined

In [21]:
n=5
l=int(len(X)/n)+1
count=1
for i in range(0, len(X), l):
    print("Fold "+str(count))
    count+=1
    train_X = None
    train_Y = None
    if(i-1>0):
        train_X = X[0:i-1]+X[i+l+1:len(X)]
        train_Y = Y[0:i-1]+Y[i+l+1:len(X)]
    else:
        train_X = X[i + l+1:len(X)]
        train_Y = Y[i + l+1:len(X)]
#     c = list(zip(train_X,train_Y))
#     shuffle(c)
#     shuffled_train_data,shuffled_train_labels = zip(*c)
    
    parameters = {'kernel':('poly','linear', 'rbf'), 'C':[1, 10]}
    svc = SVC(gamma="scale")
    clf = GridSearchCV(svc, parameters,scoring='accuracy', cv=5)
    clf.fit(train_X,train_Y)
    
    best_parameters = clf.best_params_  
    print("Best Parameters: "+str(best_parameters))
    
    best_score = clf.best_score_
    print("Best Score: "+str(best_score))

Fold 1
Best Parameters: {'C': 1, 'kernel': 'rbf'}
Best Score: 0.9041834333004327
Fold 2
Best Parameters: {'C': 1, 'kernel': 'linear'}
Best Score: 0.8804100227790432
Fold 3
Best Parameters: {'C': 1, 'kernel': 'rbf'}
Best Score: 0.8953682611996963
Fold 4
Best Parameters: {'C': 10, 'kernel': 'rbf'}
Best Score: 0.8880030372057707
Fold 5
Best Parameters: {'C': 10, 'kernel': 'rbf'}
Best Score: 0.8770398481973435


In [22]:
clf.fit(X[i:i+l],Y[i:i+l])

GridSearchCV(cv=5, error_score='raise-deprecating',
       estimator=SVC(C=1.0, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma='scale', kernel='rbf',
  max_iter=-1, probability=False, random_state=None, shrinking=True,
  tol=0.001, verbose=False),
       fit_params=None, iid='warn', n_jobs=None,
       param_grid={'kernel': ('poly', 'linear', 'rbf'), 'C': [1, 10]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring='accuracy', verbose=0)

In [23]:
train_predictions = clf.predict(TEST)
s=accuracy_score(GT, train_predictions)
print("Accuracy:"+str(s))

Accuracy:0.12273991655076495


In [7]:
print("Hello")

Hello


In [8]:
n=5
scores=[]
l=int(len(TEST)/n)+1
count=1
for i in range(0, len(TEST), l):
    print("Fold "+str(count))
    count+=1
    train_X = None
    train_Y = None
    if(i-1>0):
        train_X = TEST[0:i-1]+TEST[i+l+1:len(TEST)]
        train_Y = GT[0:i-1]+GT[i+l+1:len(TEST)]        
    else:
        train_X = TEST[i + l+1:len(TEST)]
        train_Y = GT[i + l+1:len(TEST)]
    val_X = TEST[i:i + l]
    val_Y = GT[i:i + l]
#     c = list(zip(train_X,train_Y))
#     shuffle(c)
#     shuffled_train_data,shuffled_train_labels = zip(*c)
#     c = list(zip(val_X,val_Y))
#     shuffle(c)
#     shuffled_val_data,shuffled_val_labels = zip(*c)
    

    svc = SVC(C=1,kernel='rbf',gamma="scale")
    svc.fit(train_X,train_Y)
    train_predictions = svc.predict(val_X)
    s=accuracy_score(val_Y, train_predictions)
    scores.append(s)
    
accuracy = np.mean(scores)
print("Accuracy:"+str(accuracy))

Fold 1
Fold 2
Fold 3
Fold 4
Fold 5
Accuracy:0.03398522381573229


K-Fold Cross-Validation + Grid Search CV
Fold 1
Best Parameters: {'C': 1, 'kernel': 'rbf'}
Best Score: 0.9041834333004327
Fold 2
Best Parameters: {'C': 1, 'kernel': 'linear'}
Best Score: 0.8804100227790432
Fold 3
Best Parameters: {'C': 1, 'kernel': 'rbf'}
Best Score: 0.8953682611996963
Fold 4
Best Parameters: {'C': 10, 'kernel': 'rbf'}
Best Score: 0.8880030372057707
Fold 5
Best Parameters: {'C': 10, 'kernel': 'rbf'}
Best Score: 0.8770398481973435

Cross-Validation Accuracy for tuned parameters:
Accuracy:0.3862490703369671

Test time accuracy:
Accuracy:0.3996291145108948

Testing with the training and testing datasets flipped.
Training on test data:
Fold 1
Fold 2
Fold 3
Fold 4
Fold 5
Accuracy:0.03398522381573229

Accuracy on training dataset:
Accuracy:0.3735576339123041


In [12]:
svc = SVC(C=1,kernel='rbf',gamma="scale")
svc.fit(TEST,GT)
train_predictions = svc.predict(X)
s=accuracy_score(Y, train_predictions)
    
print("Accuracy:"+str(s))

Accuracy:0.005101421110166404


In [15]:
TEST

[array([5.77716640e-03, 5.50206327e-04, 3.02613483e-03, 6.32737291e-03,
        1.65061904e-03, 1.10041263e-02, 2.20082531e-03, 4.67675387e-03,
        1.37551579e-02, 1.98074285e-02, 2.06327364e-02, 3.93397537e-02,
        3.08115548e-02, 7.92297139e-02, 6.21733161e-02, 5.19944995e-02,
        3.93397537e-02, 6.76753773e-02, 2.25584591e-02, 3.32874822e-02,
        2.75103158e-02, 3.21870692e-02, 5.80467673e-02, 1.81568090e-02,
        3.63136179e-02, 1.12792296e-02, 2.64099046e-02, 8.80330123e-03,
        9.90371424e-03, 2.33837689e-02, 9.07840448e-03, 2.75103158e-02,
        1.40302611e-02, 4.12654727e-02, 3.90646504e-02, 6.96011038e-02,
        5.77716640e-02, 6.13480063e-02, 8.99587369e-02, 8.99587369e-02,
        1.11966990e-01, 1.05639619e-01, 8.39064654e-02, 1.13067403e-01,
        9.02338365e-02, 7.26272359e-02, 7.75790944e-02, 4.56671247e-02,
        4.51169182e-02, 3.71389277e-02, 3.87895472e-02, 2.86107288e-02,
        1.56808806e-02, 1.23796426e-02, 7.70288869e-03, 1.513067

In [16]:
GT

[8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,
 8,


In [10]:
n=5
scores=[]
l=int(len(X)/n)+1
count=1
for i in range(0, len(X), l):
    print("Fold "+str(count))
    count+=1
    train_X = None
    train_Y = None
    if(i-1>0):
        train_X = X[0:i-1]+X[i+l+1:len(X)]
        train_Y = Y[0:i-1]+Y[i+l+1:len(X)]        
    else:
        train_X = X[i + l+1:len(X)]
        train_Y = Y[i + l+1:len(X)]
    val_X = X[i:i + l]
    val_Y = Y[i:i + l]
#     c = list(zip(train_X,train_Y))
#     shuffle(c)
#     shuffled_train_data,shuffled_train_labels = zip(*c)
#     c = list(zip(val_X,val_Y))
#     shuffle(c)
#     shuffled_val_data,shuffled_val_labels = zip(*c)
    

    svc = SVC(C=1,kernel='rbf',gamma="scale")
    svc.fit(train_X,train_Y)
    train_predictions = svc.predict(val_X)
    s=accuracy_score(val_Y, train_predictions)
    scores.append(s)
    
accuracy = np.mean(scores)
print("Accuracy:"+str(accuracy))

Fold 1
Fold 2
Fold 3
Fold 4
Fold 5
Accuracy:0.3862490703369671


In [11]:
svc = SVC(C=1,kernel='rbf',gamma="scale")
svc.fit(X,Y)
train_predictions = svc.predict(X)
s=accuracy_score(Y, train_predictions)
    
print("Accuracy:"+str(s))

Accuracy:0.9919834811125956


In [328]:
# n=5
# l=int(len(X)/n)+1
# count=1
# for i in range(0, len(X), l):
#     print("Fold "+str(count))
#     count+=1
#     train_X = None
#     train_Y = None
#     if(i-1>0):
#         train_X = X[0:i-1]+X[i+l+1:len(X)]
#         train_Y = Y[0:i-1]+Y[i+l+1:len(X)]
#     else:
#         train_X = X[i + l+1:len(X)]
#         train_Y = Y[i + l+1:len(X)]
# #     c = list(zip(train_X,train_Y))
# #     shuffle(c)
# #     shuffled_train_data,shuffled_train_labels = zip(*c)
    
parameters = {'bootstrap': [True],
'max_depth': [80, 90, 100, 110],
'max_features': [2, 3],
'min_samples_leaf': [3, 4, 5],
'min_samples_split': [8, 10, 12],
'n_estimators': [100, 200, 300, 1000]}
rfc = RandomForestClassifier()
clf = GridSearchCV(rfc, parameters, cv=5)
clf.fit(X,Y)

best_parameters = clf.best_params_  
print("Best Parameters: "+str(best_parameters))

best_score = clf.best_score_
print("Best Score: "+str(best_score))

Best Parameters: {'bootstrap': True, 'max_depth': 110, 'max_features': 2, 'min_samples_leaf': 4, 'min_samples_split': 12, 'n_estimators': 100}
Best Score: 0.9642779822472397


In [26]:
n=5
scores=[]
l=int(len(X)/n)+1
count=1
for i in range(0, len(X), l):
    print("Fold "+str(count))
    count+=1
    train_X = None
    train_Y = None
    if(i-1>0):
        train_X = X[0:i-1]+X[i+l+1:len(X)]
        train_Y = Y[0:i-1]+Y[i+l+1:len(X)]        
    else:
        train_X = X[i + l+1:len(X)]
        train_Y = Y[i + l+1:len(X)]
    val_X = X[i:i + l]
    val_Y = Y[i:i + l]
    c = list(zip(train_X,train_Y))
    shuffle(c)
    shuffled_train_data,shuffled_train_labels = zip(*c)
    c = list(zip(val_X,val_Y))
    shuffle(c)
    shuffled_val_data,shuffled_val_labels = zip(*c)
    

    rfc = RandomForestClassifier(bootstrap= True, 
                                 max_depth= 110, 
                                 max_features= 2, 
                                 min_samples_leaf= 4, 
                                 min_samples_split= 12, 
                                 n_estimators= 100)
    rfc.fit(shuffled_train_data,shuffled_train_labels)
    train_predictions = rfc.predict(val_X)
    s=accuracy_score(val_Y, train_predictions)
    scores.append(s)
    
accuracy = np.mean(scores)
print("Accuracy:"+str(accuracy))

Fold 1
Fold 2
Fold 3
Fold 4
Fold 5
Accuracy:0.3580016720093455


In [27]:
rfc = RandomForestClassifier(bootstrap= True, 
                                 max_depth= 110, 
                                 max_features= 2, 
                                 min_samples_leaf= 4, 
                                 min_samples_split= 12, 
                                 n_estimators= 100)
rfc.fit(X,Y)
train_predictions = rfc.predict(TEST)
s=accuracy_score(GT, train_predictions)
    
print("Accuracy:"+str(s))

Accuracy:0.4596082522021326


In [30]:
knn = KNeighborsClassifier(16)
knn.fit(X,Y)
train_predictions = knn.predict(TEST)
accuracy_score(GT, train_predictions)

0.3889082058414465